In [40]:
# Imports 
import pandas as pd
import numpy as np
import time
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_error
from sklearn.neighbors import NearestNeighbors
from scipy.sparse import csr_matrix
import operator

In [41]:
# load the data, keep only selected columns
# Read the file using super fast Pandas.read_csv
def load_required_data(path, required_columns):
    dataframe = pd.read_json(path, lines=True)
    dataframe = dataframe[required_columns]
    return dataframe, dataframe.values

In [42]:
dataframe, values = load_required_data('../train.json', ["asin", "reviewerID", "overall"])

In [43]:
dataframe[:10]

asin             reviewerID  overall
0  B00AMR1HZ8  A00100742Q4O8VH0YMUBZ        4
1  B006C1ZSO4  A00100742Q4O8VH0YMUBZ        5
2  B00ANT8OF6  A00100742Q4O8VH0YMUBZ        4
3  B008LY1B32  A00100742Q4O8VH0YMUBZ        4
4  B0080JJLBW  A00100742Q4O8VH0YMUBZ        5
5  B007KPT2N4  A00100742Q4O8VH0YMUBZ        1
6  B00EQ2TYMS  A00100742Q4O8VH0YMUBZ        4
7  B007PW1BRC  A00100742Q4O8VH0YMUBZ        2
8  B009P8EMCK  A00100742Q4O8VH0YMUBZ        5
9  B006YUVTK0  A00100742Q4O8VH0YMUBZ        5

In [44]:
dataframe.shape

(665666, 3)

In [45]:
# Create user-item matrix given a matrix and mapping from original matrix columns to new matrix rows/columns
def create_user_item_matrix(data, rowMapping, columnMapping):
    # Create table of users to items by taking row and column pivots
    # Rows of user-item table are users
    rows, row_pos = np.unique(data[:, rowMapping], return_inverse=True)
    # Columns of user-item table are movies
    cols, col_pos = np.unique(data[:, columnMapping], return_inverse=True)

    pivot_table = np.zeros((len(rows), len(cols)), dtype=data.dtype)
    pivot_table[row_pos, col_pos] = data[:, 2]
    return pivot_table, rows, cols

In [46]:
ratings_matrix, rows, cols = create_user_item_matrix(values, rowMapping=1, columnMapping=0)
print (ratings_matrix.shape)

(87271, 13209)


In [47]:
pd.DataFrame(ratings_matrix[:10], index = rows[:10], columns= cols)

B004A9SDD8 B004AFQAUA B004AHBBPW B004ALVL6W B004AMAIZQ  \
A00100742Q4O8VH0YMUBZ          0          0          0          0          0   
A001619027H9L9EG4UVRB          0          0          0          0          0   
A002359833QJM7OQHCXWY          0          0          0          0          0   
A0037670NPLI11RBWYFA           0          0          0          0          0   
A003841815JTX0JFLR8B1          0          0          0          0          0   
A0038872349TB5N0JHQQW          0          0          0          0          0   
A00455683H6M1GQZMPQPV          0          0          0          0          0   
A0047670XAAJD587LXS7           0          0          0          0          0   
A00501041JRAPWYLPQ4TE          0          0          0          0          0   
A00507662MEMHI1YMGQ15          0          0          0          0          0   

                      B004AMDC86 B004ANC00Q B004ANE2WU B004ANMWPY B004AZH4C8  \
A00100742Q4O8VH0YMUBZ          0          0          0          0          0   
A001619027H9L9EG4UVRB          0          0          0          0          0   
A002359833QJM7OQHCXWY          0          0          0          0          0   
A0037670NPLI11RBWYFA           0          0          0          0          0   
A003841815JTX0JFLR8B1          0          0          0          0          0   
A0038872349TB5N0JHQQW          0          0          0          0          0   
A00455683H6M1GQZMPQPV          0          0          0          0          0   
A0047670XAAJD587LXS7           0          0          0          0          0   
A00501041JRAPWYLPQ4TE          0          0          0          0          0   
A00507662MEMHI1YMGQ15          0          0          0          0          0   

                         ...     B00LDNE3FG B00LDNQHJ6 B00LEIT6K2 B00LFLOEYG  \
A00100742Q4O8VH0YMUBZ    ...              0          0          0          0   
A001619027H9L9EG4UVRB    ...              0          0          0          0   
A002359833QJM7OQHCXWY    ...              0          0          0          0   
A0037670NPLI11RBWYFA     ...              0          0          0          0   
A003841815JTX0JFLR8B1    ...              0          0          0          0   
A0038872349TB5N0JHQQW    ...              0          0          0          0   
A00455683H6M1GQZMPQPV    ...              0          0          0          0   
A0047670XAAJD587LXS7     ...              0          0          0          0   
A00501041JRAPWYLPQ4TE    ...              0          0          0          0   
A00507662MEMHI1YMGQ15    ...              0          0          0          0   

                      B00LIAMYCI B00LITLOMK B00LMLW8T2 B00LMLXTJK B00LP1MVSW  \
A00100742Q4O8VH0YMUBZ          0          0          0          0          0   
A001619027H9L9EG4UVRB          0          0          0          0          0   
A002359833QJM7OQHCXWY          0          0          0          0          0   
A0037670NPLI11RBWYFA           0          0          0          0          0   
A003841815JTX0JFLR8B1          0          0          0          0          0   
A0038872349TB5N0JHQQW          0          0          0          0          0   
A00455683H6M1GQZMPQPV          0          0          0          0          0   
A0047670XAAJD587LXS7           0          0          0          0          0   
A00501041JRAPWYLPQ4TE          0          0          0          0          0   
A00507662MEMHI1YMGQ15          0          0          0          0          0   

                      B00LUEMK44  
A00100742Q4O8VH0YMUBZ          0  
A001619027H9L9EG4UVRB          0  
A002359833QJM7OQHCXWY          0  
A0037670NPLI11RBWYFA           0  
A003841815JTX0JFLR8B1          0  
A0038872349TB5N0JHQQW          0  
A00455683H6M1GQZMPQPV          0  
A0047670XAAJD587LXS7           0  
A00501041JRAPWYLPQ4TE          0  
A00507662MEMHI1YMGQ15          0  

[10 rows x 13209 columns]

In [48]:
def get_index_map(arr):
    index_map = {}
    for el in arr:
        index_map[el] = len(index_map)
    return index_map

In [49]:
# Get unique movies and users
unique_items = np.unique(values[:,0])
unique_users = np.unique(values[:,1])

In [50]:
unique_items.shape

(13209,)

In [51]:
unique_users.shape

(87271,)

In [53]:
mean_overall = np.true_divide(ratings_matrix.sum(),(ratings_matrix!=0).sum())

In [54]:
def get_users_who_rated_item(item_id):
    return np.where(ratings_matrix[:,item_idx_map[item_id]] > 0)[0]

def get_users_who_rated_item_by_index(item_idx):
    return np.where(ratings_matrix[:,item_idx] > 0)

def predict(user_id, item_id):
    return mean_overall

In [59]:
test_dataframe, test_values = load_required_data('../test.json', ["asin", "reviewerID", "overall"])

In [60]:
test_dataframe['reviewerID'].unique().shape

(87271,)

In [61]:
# Returns DF containing predictions, MAE, RMSE
def get_predictions(dataframe):
    df = dataframe.copy()
    print ("Predicting ratings..")
    start_time = time.time()
    df['Prediction'] = df.apply(lambda row: predict_row(row) , axis=1)
    MAE = round(mean_absolute_error(df['overall'], df['Prediction']), 2)
    RMSE = round(np.sqrt(mean_squared_error(df['overall'], df['Prediction'])), 2)
    print "Done Predicting in",  round((time.time() - start_time), 2), "seconds"
    return df, MAE, RMSE

i = 0
def predict_row(row):
    global i
    i+= 1
    prediction = predict(row['reviewerID'], row['asin'])
    print ("#", i, "Actual = ", row['overall'], "Predictioned = ", prediction)
    return prediction

In [62]:
df, MAE, RMSE = get_predictions(test_dataframe)

Predicting ratings..
('#', 1, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 2, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 3, 'Actual = ', 3, 'Predictioned = ', 3.9629303584680606)
('#', 4, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 5, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 6, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 7, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 8, 'Actual = ', 3, 'Predictioned = ', 3.9629303584680606)
('#', 9, 'Actual = ', 3, 'Predictioned = ', 3.9629303584680606)
('#', 10, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 11, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 12, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 13, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 14, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 15, 'Actual = ', 1, 'Predictioned = ', 3.9629303584680606)
('#', 16, 'Ac

('#', 353, 'Actual = ', 3, 'Predictioned = ', 3.9629303584680606)
('#', 354, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 355, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 356, 'Actual = ', 3, 'Predictioned = ', 3.9629303584680606)
('#', 357, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 358, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 359, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 360, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 361, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 362, 'Actual = ', 1, 'Predictioned = ', 3.9629303584680606)
('#', 363, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 364, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 365, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 366, 'Actual = ', 1, 'Predictioned = ', 3.9629303584680606)
('#', 367, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 368,

('#', 1758, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 1759, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 1760, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 1761, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 1762, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 1763, 'Actual = ', 3, 'Predictioned = ', 3.9629303584680606)
('#', 1764, 'Actual = ', 2, 'Predictioned = ', 3.9629303584680606)
('#', 1765, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 1766, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 1767, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 1768, 'Actual = ', 3, 'Predictioned = ', 3.9629303584680606)
('#', 1769, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 1770, 'Actual = ', 1, 'Predictioned = ', 3.9629303584680606)
('#', 1771, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 1772, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680

('#', 3158, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 3159, 'Actual = ', 2, 'Predictioned = ', 3.9629303584680606)
('#', 3160, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 3161, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 3162, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 3163, 'Actual = ', 1, 'Predictioned = ', 3.9629303584680606)
('#', 3164, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 3165, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 3166, 'Actual = ', 2, 'Predictioned = ', 3.9629303584680606)
('#', 3167, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 3168, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 3169, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 3170, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 3171, 'Actual = ', 1, 'Predictioned = ', 3.9629303584680606)
('#', 3172, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680

('#', 4666, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 4667, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 4668, 'Actual = ', 2, 'Predictioned = ', 3.9629303584680606)
('#', 4669, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 4670, 'Actual = ', 1, 'Predictioned = ', 3.9629303584680606)
('#', 4671, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 4672, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 4673, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 4674, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 4675, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 4676, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 4677, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 4678, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 4679, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 4680, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680

...

('#', 80564, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 80565, 'Actual = ', 1, 'Predictioned = ', 3.9629303584680606)
('#', 80566, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 80567, 'Actual = ', 2, 'Predictioned = ', 3.9629303584680606)
('#', 80568, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 80569, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 80570, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 80571, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 80572, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 80573, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 80574, 'Actual = ', 2, 'Predictioned = ', 3.9629303584680606)
('#', 80575, 'Actual = ', 1, 'Predictioned = ', 3.9629303584680606)
('#', 80576, 'Actual = ', 1, 'Predictioned = ', 3.9629303584680606)
('#', 80577, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 80578, 'Actual = ', 5, 'Predictioned = ', 

('#', 82103, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 82104, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 82105, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 82106, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 82107, 'Actual = ', 3, 'Predictioned = ', 3.9629303584680606)
('#', 82108, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 82109, 'Actual = ', 1, 'Predictioned = ', 3.9629303584680606)
('#', 82110, 'Actual = ', 1, 'Predictioned = ', 3.9629303584680606)
('#', 82111, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 82112, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 82113, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 82114, 'Actual = ', 3, 'Predictioned = ', 3.9629303584680606)
('#', 82115, 'Actual = ', 2, 'Predictioned = ', 3.9629303584680606)
('#', 82116, 'Actual = ', 1, 'Predictioned = ', 3.9629303584680606)
('#', 82117, 'Actual = ', 5, 'Predictioned = ', 

('#', 83269, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 83270, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 83271, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 83272, 'Actual = ', 1, 'Predictioned = ', 3.9629303584680606)
('#', 83273, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 83274, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 83275, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 83276, 'Actual = ', 3, 'Predictioned = ', 3.9629303584680606)
('#', 83277, 'Actual = ', 3, 'Predictioned = ', 3.9629303584680606)
('#', 83278, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 83279, 'Actual = ', 1, 'Predictioned = ', 3.9629303584680606)
('#', 83280, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 83281, 'Actual = ', 2, 'Predictioned = ', 3.9629303584680606)
('#', 83282, 'Actual = ', 1, 'Predictioned = ', 3.9629303584680606)
('#', 83283, 'Actual = ', 5, 'Predictioned = ', 

('#', 84630, 'Actual = ', 3, 'Predictioned = ', 3.9629303584680606)
('#', 84631, 'Actual = ', 3, 'Predictioned = ', 3.9629303584680606)
('#', 84632, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 84633, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 84634, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 84635, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 84636, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 84637, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 84638, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 84639, 'Actual = ', 3, 'Predictioned = ', 3.9629303584680606)
('#', 84640, 'Actual = ', 3, 'Predictioned = ', 3.9629303584680606)
('#', 84641, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 84642, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 84643, 'Actual = ', 2, 'Predictioned = ', 3.9629303584680606)
('#', 84644, 'Actual = ', 2, 'Predictioned = ', 

('#', 85789, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 85790, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 85791, 'Actual = ', 1, 'Predictioned = ', 3.9629303584680606)
('#', 85792, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 85793, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 85794, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 85795, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 85796, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 85797, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 85798, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 85799, 'Actual = ', 3, 'Predictioned = ', 3.9629303584680606)
('#', 85800, 'Actual = ', 4, 'Predictioned = ', 3.9629303584680606)
('#', 85801, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 85802, 'Actual = ', 5, 'Predictioned = ', 3.9629303584680606)
('#', 85803, 'Actual = ', 5, 'Predictioned = ', 

In [63]:
print "MAE=", MAE
print "RMSE=", RMSE

MAE= 1.06
RMSE= 1.32


In [29]:
sparse_ratings = csr_matrix(ratings_matrix, dtype='float')

In [30]:
model_knn = NearestNeighbors(metric = 'cosine', n_neighbors = 6)
model_knn.fit(sparse_ratings)

NearestNeighbors(algorithm='auto', leaf_size=30, metric='cosine',
         metric_params=None, n_jobs=1, n_neighbors=6, p=2, radius=1.0)

In [31]:
def get_recommendations(user_index, n_reccomendations=5, n_neighbors=10):
    distances,indices = model_knn.kneighbors(ratings_matrix[user_index].reshape(1, -1), n_neighbors=n_neighbors)
    probable_items = list()
    for user in indices[0]:
        if user == user_index:
            #print "Recommendations for user ", unique_users[user_index]
            continue
        # all other users
        for items in np.nonzero(ratings_matrix[user]):
            for item in items:
                if ratings_matrix[user_index][item] == 0:
                    probable_items.append(unique_items[item])

    predictions = {}
    for item in probable_items:
        predictions[item] = predict(unique_users[0], item)
        sorted_predictions = sorted(predictions.items(), key=operator.itemgetter(1))
    return [i[0] for i in sorted_predictions[:n_reccomendations]]

In [32]:
def get_user_items_rated_df(user_id):
    df = pd.DataFrame()
    np.nonzero(ratings_matrix[user_id])
    for i in np.nonzero(ratings_matrix[user_id]):
        x = pd.DataFrame({"item":unique_items[i], "rating":ratings_matrix[user_id][i]})
        df = df.append(x)
        return df

def print_items_rated(user_id):
    np.nonzero(ratings_matrix[user_id])
    for i in unique_items[np.nonzero(ratings_matrix[user_id])]:
        print i

In [33]:
get_user_items_rated_df(0)

item rating
0  B000EH4V18      5
1  B0014FKI1Q      4
2  B00353PWAW      4
3  B0062BHOOG      4

In [34]:
print get_recommendations(user_index=0)
import asin_to_rec
asin_to_rec.get_recommendation_items(get_recommendations(user_index=0)[:2])

[u'B00265FXTA', u'B0002YTN4I', u'B0031B4YU2', u'B0009IQZFM', u'B000XETMW0']
